# Doc2Vec-представления определений

Подготовим смешанный датасет с определениями:

In [1]:
import pandas as pd

file1 = 'test_set_002.csv'

data = pd.read_csv(file1, delimiter=',')

print(data.shape)
data.head(5)

(26861, 3)


defs          word  len
0                     колпак на лампе        абажур   15
1  настоятель католического монастыря         аббат   34
2              католический священник         аббат   22
3              католический монастырь     аббатство   22
4                слово из первых букв  аббревиатура   20

In [2]:
data['defs'] += ' формальное'
data.head()

defs          word  len
0                     колпак на лампе формальное        абажур   15
1  настоятель католического монастыря формальное         аббат   34
2              католический священник формальное         аббат   22
3              католический монастырь формальное     аббатство   22
4                слово из первых букв формальное  аббревиатура   20

In [3]:
del data['len']
data.head()

defs          word
0                     колпак на лампе формальное        абажур
1  настоятель католического монастыря формальное         аббат
2              католический священник формальное         аббат
3              католический монастырь формальное     аббатство
4                слово из первых букв формальное  аббревиатура

In [4]:
file2 = '004_human_set_3000.csv'

human_data = pd.read_csv(file2, comment='#')
human_data.head()

word                                               defs
0     абажур                                верхняя часть лампы
1     абажур                                        часть лампы
2  абонемент  это карточка, которая позволяет тебе ходить в ...
3    абрикос                          маленький оранжевый фрукт
4    абрикос                                              фрукт

In [5]:
human_data['defs'] += ' неформальное'
human_data.head()

word                                               defs
0     абажур                   верхняя часть лампы неформальное
1     абажур                           часть лампы неформальное
2  абонемент  это карточка, которая позволяет тебе ходить в ...
3    абрикос             маленький оранжевый фрукт неформальное
4    абрикос                                 фрукт неформальное

In [6]:
mix_data = pd.concat([data, human_data], sort=True)

mix_data.head()

defs          word
0                     колпак на лампе формальное        абажур
1  настоятель католического монастыря формальное         аббат
2              католический священник формальное         аббат
3              католический монастырь формальное     аббатство
4                слово из первых букв формальное  аббревиатура

Теперь построим векторные представления имеющихся определений с помощью doc2vec

In [8]:
from gensim.models.doc2vec import Doc2Vec, TaggedDocument
from string import punctuation
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
import spacy

stops = stopwords.words("russian")

nlp = spacy.load('ru2')
nlp.add_pipe(nlp.create_pipe('sentencizer'), first=True)

defs = []
_id = 0

for sentence in mix_data['defs']:
    text = ''.join(x for x in sentence if x not in punctuation)
    words = word_tokenize(text, language="russian")
    words = [word for word in words if word not in stops]
    text = ' '.join(words)
    doc = nlp(text)
    words = [word.lemma_ for word in nlp(text)]
    
    defs.append(TaggedDocument(words=words, tags=[_id]))
    _id += 1
        
d2v_model = Doc2Vec(vector_size=300, window=5, min_count=1, workers=4)
d2v_model.build_vocab(defs)
d2v_model.train(defs, total_examples=d2v_model.corpus_count, epochs=d2v_model.epochs)

Сохраним получившуюся модель:

In [9]:
import pickle

with open('d2v_model.pickle', 'wb') as file:
    pickle.dump(d2v_model, file)

# Кластеризация

In [21]:
from sklearn_extra.cluster import KMedoids
import numpy as np

vec_arr = []
for i in range(_id):
    vec_arr.append(d2v_model[i])
X = np.asarray(vec_arr)
kmedoids = KMedoids(n_clusters=5,metric='cosine').fit(X)

mix_data['#cluster'] = kmedoids.labels_

In [22]:
mix_data.to_csv('clusters_d2v_5.csv')

Посмотрим, какие кластеры получились:

In [28]:
for sent in mix_data.loc[mix_data['#cluster'] == 0]['defs']:
    print(sent)

текст с красной строки формальное
представитель абстракционизма формальное
передовая часть формальное
расстояние, которое проходит судно за один оборот гребного винта формальное
, почтительное обращение детей к родителям; отец формальное
авиационный двигатель формальное
работник автомобильного завода формальное
; внедрение автомобилей в жизнь людей формальное
спортсмен, занимающийся автомобильным спортом формальное
способность выполнять какие-либо действия без сознательного контроля формальное
сфера торговли автомобилями формальное
представитель некоего учреждения, организации и т. п., выполняющий поручения; лицо, действующее по поручению и в интересах кого-либо; уполномоченный формальное
деятельность такой группы формальное
группа, команда, сообщество агентов формальное
член Аграрной партии формальное
банк, ведущий финансовую деятельность в агропромышленной отрасли формальное
, буква формальное
авторитетная научная или художественная организация формальное
разновидность высшего учебно

Про нулевой кластер: из неформальных попали определения, состоящие из одного слова, определения-признаки (что можно делать с этим объектом, на что он похож), определения с пропусками, короткие определения вида "прилагательное+существительное"; из формальных -- в основном, короткие определения

In [29]:
for sent in mix_data.loc[mix_data['#cluster'] == 1]['defs']:
    print(sent)

настоятель католического монастыря формальное
католический монастырь формальное
сокращение формальное
искажение изображения формальное
поступающий в университет формальное
подписка формальное
отдел библиотеки, где книги выдаются на дом формальное
штурм корабля формальное
магическое заклинание формальное
кавказский горец формальное
контурный рисунок формальное
внешние очертания формальное
возведение в формальное
направление в искусстве, отказывающееся от реалистических образов формальное
нечто нематериальное формальное
бред формальное
нелепость, бессмысленность формальное
житель абхазии формальное
авангардистское искусство формальное
передовой отряд формальное
стремление возглавить что-либо, занять доминирующие позиции в каком-либо движении, течении и т. п. формальное
художественное направление, сознательно отрывающееся от классических академичных принципов в поисках выразительных форм и средств формальное
сторонник, последователь авангардизма формальное
передняя, открытая часть сцены, 

, попытка поднятием руки остановить проезжающее транспортное средство формальное
; тихий, слабый голос формальное
гомосексуальность, гомосексуальные отношения, гомосексуальное поведение; лицо гомосексуальной ориентации формальное
ягоды этого растения формальное
обращение к женщине формальное
любимая, возлюбленная формальное
самка голубя формальное
ласково-фамильярное обращение к мужчине формальное
, беднота, бедные люди либо бедный человек формальное
бедность, нищета формальное
короткий чулок с резинкой, охватывающей ногу под коленом формальное
тот, кто лечит методами гомеопатии, считает себя специалистом в ней формальное
метод лечения болезней минимальными дозами лекарств, которые в больших дозах вызывают в организме здорового человека явления, сходные с признаками данной болезни формальное
лекарственные препараты, применяемые при таком методе лечения формальное
саморегуляция, способность открытой системы сохранять постоянство своего внутреннего состояния, характеристик посредством ск

бумажный пакет для хранения сыпучих веществ формальное
узел механизма в виде вращающегося диска или цилиндра формальное
развлекательный аттракцион, вращающаяся площадка с сиденьями в виде лошадок, лодок и т. п. для катанья формальное
совокупность горных выработок, образованных при добыче полезного ископаемого открытым способом формальное
совокупность чьих-либо достижений в продвижении по службе, упрочнении статуса формальное
птица семейства ласточек отряда воробьиных с крайними рулевыми перьями в виде косиц формальное
стремительный, неудержимый поток чего-либо (слов, звуков и прочее) формальное
группа последовательно соединенных однотипных устройств, сооружений, объектов формальное
место, кабинка, где стоит этот аппарат и находится обслуживающий его работник формальное
ящик, шкаф для хранения денег и ценных бумаг формальное
аппарат, на котором отпечатываются талоны с указанием полученной суммы, формальное
денежная наличность учреждения, предприятия формальное
проверка вышестоящим судом

машина для обмолота, молотьбы различных сельскохозяйственных культур формальное
кузнец, работающий большим ручным молотом формальное
слуховая косточка среднего уха формальное
беспощадная, ненасытная сила, требующая беспрестанных человеческих жертв формальное
растение семейства молочайных (), в стеблях и листьях которого содержится ядовитый млечный сок формальное
косметическое средство в виде жидкого крема белого цвета формальное
жидкость, образующаяся в зобу или в особых железах некоторых птиц и насекомых для кормления птенцов, личинок формальное
молчаливый, неразговорчивый человек формальное
монах, отшельник, давший обет молчания формальное
, то есть воздержание от речи, высказываний, использования голоса формальное
молчаливый, неразговорчивый человек формальное
; горячая, страстная просьба формальное
подставка (обычно треножная), на которой помещается подрамник с холстом, картоном или доской для работы художника формальное
клетка, имеющая жгуты формальное
форма государственного управ

то, что дарят, что подарено формальное
тот, кто собственноручно предъявляет по назначению письмо, документ и т. п. формальное
в теннисе и т.д. введение мяча в игру формальное
совокупность атрибутов процесса передачи некоего массива информации (формы, структуры, стиля, трактовки, оперативности...) формальное
пожертвование, которое делают кому-нибудь из милости, из сострадания; милостыня формальное
то, чем подшивается что-либо с изнанки, снизу; подкладка формальное
каблук, сделанный из кусков кожи формальное
сочетание (красок, расцветок и т. п.) формальное
, подобрать, подбираться, подобраться формальное
то, что подобрано; коллекция, собрание, ассортимент, набор формальное
то, что подвешено, висит для украшения или по необходимости формальное
тонкое приспособление для подвешивания чего-либо формальное
, какая-либо проделка, нелепый, неблаговидный поступок формальное
самоотверженный, героический поступок формальное
небольшое смещение, продвижение (льда, почвы) формальное
тот, кто изнуряет

короткометражный кино-, видео- или анимационный фильм рекламного, информационного и т. п. содержания формальное
роликовые коньки формальное
блюдо японской кухни (разновидность суши), представляющее собой разрезанный на кусочки рулет из риса и прессованных водорослей с начинкой формальное
сводный текст выделенных из пьес слов (монологов, реплик) одного персонажа формальное
литературное (обычно прозаическое) произведение с развернутым повествованием о жизни и развитии личности главного героя формальное
юрист, специалист по римскому праву формальное
лирическое стихотворение песенного народного склада (в западноевропейской литературе эпохи Средневековья и в подражательной поэзии позднейших времен) формальное
небольшое произведение для голоса с сопровождением фортепиано или каких-либо других инструментов (гитары, арфы и т. п.) формальное
небольшая музыкальная пьеса с преобладанием мелодии песенного лирического характера формальное
мироощущение, умонастроение, характеризующееся идеализацией 

женский головной убор европейцев из ленты или шарфа, обмотанных вокруг высокой прически формальное
, тот, по чьему распоряжению кто-либо отправлен в тюрьму, притеснитель формальное
представитель группы родственных народов, говорящих на тюркских языках формальное
тюрьма; СИЗО (следственный изолятор) формальное
плоское гибкое покрытие, применяемое у мостов, плотин для предохранения русла реки и берегов от размыва и выполняемое из хвороста, камня, бетона и других материалов формальное
тавыт, кулик () формальное
, , вялый, нерасторопный, безвольный человек формальное
мешок, набитый мягким материалом (соломой, сеном, мочалом, волосом, ватой, пером, пухом и т. п.) и служащий постелью, подстилкой формальное
, вдох дыма при курении формальное
профилированный выступ, разделяющий стену по горизонтали или обрамляющий панно формальное
конвекционный поток воздуха в трубе, туннеле формальное
подать, тягло, повинность формальное
рычаг или трос, передающий тянущее или толкающее усилие с одного узла ко

синоним слова архитектор неформальное
он спасает от дождя неформальное
смотрит в зале в театре или кино неформальное
растет во рту неформальное
на кремлевской стене неформальное
бизон неформальное
долька чеснока неформальное
находятся во рту, человек ими жуёт неформальное
танцевальная фитнес-программа на основе популярных латиноамериканских ритмов неформальное
плакучее дерево неформальное
в куклы неформальное
штукатурка неформальное
документ, который о чем-то оповещает неформальное
сознательное причинение психологической травмы неформальное
затраты неформальное
недостаток неформальное
страна неформальное
метод математического доказательства неформальное
новая вдохновляющая мысль неформальное
интернатура неформальное
интернет-провайдер неформальное
интернет неформальное
международный розыск неформальное
кредит на квартиру неформальное
из неё разгорится пламя неформальное
грешники говорят ее священнику о своих грехах неформальное
починка неформальное
ягода малинка моя неформальное
весной

Про первый кластер: из формальных попало много длинных определений, объяснений через глаголы, определений-перечислений; из неформальных -- описания мест (через "там", "туда", где что-то делают), отсылки ("бот от яндекса", "кирка из майнкрафта", басни Крылова, картина Левитана), объяснения через глаголы, определения-"продолжи цитату", описания явлений ("когда" что-то сделано, делаешь)

In [30]:
for sent in mix_data.loc[mix_data['#cluster'] == 2]['defs']:
    print(sent)

выставка новых моделей автомобилей; помещение, в котором проходит такая выставка формальное
должностные лица, возглавляющие учреждение, предприятие, организацию формальное
цветок такого растения формальное
; точность, упорядоченность и тщательность в исполнении чего-либо, движениях формальное
орган управления таким устройством формальное
некое единичное действие, деяние, а также поступок, проявление действий формальное
точный набор инструкций, описывающих последовательность действий для достижения результата, решения задачи формальное
вещество, от которого чихаешь формальное
характер, способ, особенность какого-либо действия формальное
вид спорта, включающий такие восхождения формальное
необходимость выбора одной из таких возможностей формальное
смягчение действия толчков, ударов при помощи особых устройств формальное
красивый мальчик, юноша формальное
, , мн. ч. результаты такого исследования в письменной форме формальное
наркотик (психоделик), изготовленный из такого сырья формальное

Про второй кластер: из формальных обнаружилось много определений, начинающихся с "результат такого действия" (например, слово "бой"), "лицо, имеющее такое звание" ("генерал" и прочие воинские звания); из неформальных -- определения, описывающие "место", где что-то делают или что-то есть 

In [31]:
for sent in mix_data.loc[mix_data['#cluster'] == 3]['defs']:
    print(sent)

прерывание беременности формальное
оранжевый фрукт с большой косточкой формальное
вещество, которое поглощает воду формальное
тот, кто склонен к авантюрам; беспринципный делец формальное
повреждение, поломка детали, механизма формальное
, духовный наставник; инок формальное
широкая улица, обсаженная по обеим сторонам деревьями (в Англии, США и некоторых других странах) формальное
предприятие, оказывающее услуги по перевозке пассажиров и грузов авиатранспортом формальное
регулярный маршрут авиаперевозок между двумя или несколькими точками формальное
общая для всего личного состава работа на судне по специальному заданию или по тревоге формальное
автотранспортное предприятие, обеспечивающее техническое обслуживание и ремонт автомобилей формальное
транспортное средство, автомобиль, предназначенный для перевозки восьми и более пассажиров формальное
осторожная, оборонительная тактика в футболе; использование почти всех полевых игроков на своей половине поля формальное
, заправочная станция;

житель, уроженец Кубани формальное
; небольшой предмет в форме куба формальное
спортивный трофей, приз в виде такого сосуда формальное
кубический метр формальное
высокий суживающийся кверху сосуд, обычно с ручкой и носиком формальное
, выдающийся мастер формальное
полая (открытая либо закрытая) часть транспортного средства, предназначенная для перевозки грузов и пассажиров формальное
, жест, при котором кисть руки сжата в кулак, а большой палец просунут между указательным и средним пальцами; обычно является вульгарным выражением отказа или вызова формальное
, щеголевато одетый, бездушный и пустой человек (обычно женщина) формальное
промежуточная стадия развития насекомых, для которых характерно полное превращение (метаморфоз) в течение жизни формальное
снайпер, действующий с огневой точки, оборудованной на дереве формальное
береговая полоса, выступающая в море мысом формальное
прибор для черчения формальное
преклонение перед кем-либо, чем-либо, почитание кого-либо, чего-либо формальное

, тот, кто выступает, произносит речь, доклад и т. п. на каком-либо мероприятии или в средствах массовой информации: докладчик, интервьюируемый и т. п. формальное
задняя (противоположная груди) часть туловища (от нижней части шеи до поясницы) человека или верхняя часть туловища животного формальное
верхняя вертикальная часть мебельного изделия (стула, кресла, кровати ), к которой сидящий человек может прислониться спиной формальное
деталь или тыльная сторона какого-либо предмета, инструмента формальное
фигура высшего пилотажа формальное
рукописная копия какого-либо оригинала формальное
очень худой человек формальное
тревожный звон, оповещающий о бедствии, сзывающий народ; набат формальное
участник, вышестоящий в иерархии по отношению к нижестоящему в иерархии формальное
тот, кто финансирует кого-либо или что-либо, выступает как поручитель, заказчик, устроитель чего-либо формальное
; обусловленность внутренними причинами; самопроизвольность формальное
, азартное увлечение чем-либо, каки

Про третий кластер: из формальных попали определения, содержащие ряды синонимов, описывающие человека; из неформальных -- опредения из одного слова, описания через признаки и действия (которые можно совершать с объектом или которые он совершает), через частные примеры, определения через антонимы

In [32]:
for sent in mix_data.loc[mix_data['#cluster'] == 4]['defs']:
    print(sent)

колпак на лампе формальное
католический священник формальное
слово из первых букв формальное
отдельный фрагмент текста формальное
нечто неотносительное формальное
превозношение формальное
форма неограниченного правления формальное
произведение абстрактного искусства, абстрактная картина формальное
отсутствие смысла, нелепость, бессмысленность формальное
гнойный нарыв, гнойник формальное
человек из народа абхазов формальное
доверие, похвала, поддержка, выраженные или высказанные заранее и требующие оправдания или подтверждения в будущем формальное
легкомысленная затея; опасное или необычное приключение, похождение формальное
искатель приключений формальное
неудача, провал, неприятность формальное
аэродром (группа аэродромов) со складами, ремонтными мастерскими и обслуживающими подразделениями для обеспечения действий авиации (обычно употребляется применительно к военной авиации) формальное
специалист, осуществляющий управление воздушным движением формальное
авиационный завод формальное


род цветковых растений семейства крапивные, отличающихся жгучестью формальное
прелести формальное
для выражения одобрения, похвалы за какой-нибудь ловкий, отличный поступок, удачное действие формальное
; покраска формальное
боец Красной гвардии формальное
ораторское искусство формальное
полная неудача, провал формальное
заведение, предоставляющее кредит, отпускающее товары в кредит формальное
крейсерская яхта формальное
приспособление, прикрепляющее лыжу к ботинку формальное
фигура в виде двух пересекающихся отрезков или полос формальное
христианский обряд крещения; празднество по случаю совершения такого обряда формальное
место пересечения двух однотипных элементов: жердей, стержней формальное
участник крестового похода формальное
сельский житель, основным занятием которого является земледелие или животноводство формальное
сельские жители, основным занятием которых является обработка земли; крестьяне формальное
низшее податное сословие, состоящее из крестьян (в царской России) формаль

руководитель церковного хора формальное
то же, что провинция формальное
утрата функций органами формальное
прибор для регулирования хода машин формальное
проверка и исправление рукописи при подготовке к печати формальное
помещение, где работает такой коллектив формальное
уменьшение размеров органа, упрощение его строения или полное исчезновение в связи с утратой его функций в процессе эволюции организма формальное
сведение сложного производственного процесса к более простому формальное
падение биржевого курса ценных бумаг или биржевых цен формальное
корнеплод этого растения, употребляемый в пищу формальное
двухлетнее травянистое растение из семейства крестоцветных с плодом в виде стручка и корнеплодом, обладающим характерным горьким вкусом формальное
условия существования, функционирования, деятельности чего-либо формальное
государственный строй, образ правления формальное
острая лопаточка, применяемая в штукатурных работах формальное
вместилище для жидкостей и газов формальное
юридиче

антоним к слову стих неформальное
произведение, больше чем рассказ неформальное
когда проигрываешь в игре неформальное
умножение чисел неформальное
работа алгоритма неформальное
несчастный случай неформальное
совокупность предприятий и фабрик неформальное
ущеле неформальное
билет внутрь неформальное
слова которые сбываются в будущем неформальное
посуда для запекания неформальное
аноним схожести неформальное
небольшой водоём неформальное
водоём неформальное
получается из клубка нитки с помощью веретена неформальное
молитва неформальное
бешеный человек неформальное
живое существо с крыльями неформальное
бывают звери, а бывают... неформальное
орудие неформальное
им переключают телевизор неформальное
ею стреляют из пистолета неформальное
метель, вьюга с сильным ветром неформальное
что-то незначительное неформальное
зимняя куртка неформальное
истязания чтобы что-то узнать неформальное
день недели неформальное
верховная в украине неформальное
цвета неформальное
ветхое, почти разваливающееся 

Про четвёртый кластер: из формальных -- короткие определения, перечисления, "тот, кто что-то делает"; из неформальных -- объяснения через глаголы и признаки, через местоположения ("во рту у боксёра", "в ней пекут пироги"), через антонимы, с пропусками ("дополни фразу")